# Programming Exercise 5: Hidden Markov Models

## Initialization

In [1]:
from wumpus_world import WumpusWorld
from main_loop import main_loop
from path_planning import PathPlanner
import maps
from typing import List, Tuple
from random import random, choice

from probability import weighted_sample_with_replacement

## Configuration
### Choose a map:
(A random map may have no possible route through)

In [2]:
# possible values: 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, "random"
world_gen = 3

if world_gen == "random":
    ww = WumpusWorld(dim_x=15, dim_y=15, wall_count=30)
else:
    ww = WumpusWorld(wall_map = getattr(maps, "map"+str(world_gen)))

## Localization

In [3]:
def tsum(a,b):
    return tuple(x+y for x,y in zip(a,b))

In [4]:
def monte_carlo_localization(movement, range_scan, samples, P_motion_sample, P_sensor, world: WumpusWorld) \
        -> List[tuple]:
    if type(samples) == int:
        samples = [world.random_free_position() for _ in range(samples)]

    # remove samples on the goal position (we can't be there)
    len_samples = len(samples)
    samples = list(filter(lambda s:s!=world.goal_pos, samples))    
    # ..and refill samples
    while len(samples) < len_samples:
        samples.append(choice(samples[:len_samples]))
    
    #TODO simulate the movement per sample with P_motion_sample() and sensor measurements with world.range_scan().
    # Resampling from samples weighted by their likelihood can be computed by weighted_sample_with_replacement().
    
    # filter unlikely samples
    weights = [P_sensor(world.range_scan(s), range_scan) for s in samples]
    samples = weighted_sample_with_replacement(len(samples), samples, weights)
    # simulate movements
    if movement is None:
        new_samples = samples
    else:
        new_samples = [P_motion_sample(s, movement, world) for s in samples]
    return new_samples
        
def P_motion_sample(position: Tuple[int,int], movement: Tuple[int,int], world: WumpusWorld) -> tuple:
    # movement is one of: (1, 0), (0, 1), (-1, 0), (0, -1)
    #TODO return position after movement
    # generate alternative movements
    altern_movs = [(1,0),(-1,0)] if movement[0] == 0 else [(0,1),(0,-1)] 
    altern = [s for s in [tsum(position,x) for x in altern_movs] if not world.wall_at(*s)]
    if len(altern) == 0: altern = [position]
    new_pos = tsum(movement, position)
    direct  = new_pos if not world.wall_at(*new_pos) else position
    
    samples = [direct] + altern
    weights = [0.8] + [0.2/len(altern) for _ in altern]
    return weighted_sample_with_replacement(1, samples, weights)[0]
    
def P_sensor(measured: int, possible_exact_value: int) -> float:
    # return conditional probability for sensor measurement, aussuming a sensor that measures
    # e.g. one uniformly selected value in (2,3,4) when the real value is 3

    return 1/3 if abs(measured - possible_exact_value) <= 1 else 0

## Simulation
### Wumpus has to find a way through the minefield:
* Valid actions are 'up','down','left' and 'right'
* Wumpus cannot completely control its actions and might go sideways to the intended direction with a chance of 20% (see problem description).
* A visualization displays the navigation through the world, as well as the weights of the samples.

In [5]:
main_loop(ww, monte_carlo_localization, P_motion_sample, P_sensor, PathPlanner(ww), loop_delay = 0.00001)

IndexError: list index out of range